# Timeless Team Ranker

So here I've created a little Timeless Cup team ranker based on PvPoke data from the top 30 ranked Timeless Cup mons in PvPoke.com, as well as implementing the frequency statistics from silph.gg (this part coming soon; they don't exist yet). All of this is done in Julia, but hopefully these little notes should clarify what the ranker is doing. I recommend running everything, and then reading through this. Some sections take a little bit of time to run (though mostly the inital data collection at 15ish seconds for 30 pokemon and the first histogram which can take a few minutes).

## Getting Started

### Installing Packages

Here I'm just grabbing some of the packages I need. I'll be reading from CSVs into DataFrames and making plots and using random distributions for uncertainty. Basically, I'm just grabbing some tools that make my life easier programming.

In [57]:
using CSV, Plots, Distributions, DataFrames, JSON, Clustering
plotly();

### Number of Pokemon

This is the number of pokemon that we are including in our model. Increasing this number increases the number of pokemon that are taken into consideration (in order of PvPoke rankings), but doing so will also increase computational time. 

In [58]:
const numMons = 45

45

### Reading Data

I've got a folder that contains all of the ranking CSVs from PvPoke, as well as the rankings JSON file. By changing individual CSVs in the folder, or updating the rankings file, we can easily modify the inputted data.

In [59]:
cd(homedir())
cd("TimelessData")
pvpokeRanks = JSON.parsefile("rankings-1500.json")
rankings = zeros(4, length(pvpokeRanks))

for f in filter(x -> startswith(x, pvpokeRanks[1]["speciesName"]), readdir())
    if(!(f in filter(x -> startswith(x, pvpokeRanks[1]["speciesName"] * " (Alolan)"), readdir())))
        rankings = CSV.read(f; delim=',');
        rename!(rankings, Symbol("Battle Rating")=>Symbol(pvpokeRanks[1]["speciesName"]))
        deletecols!(rankings, 3:4)
    end
end

for i = 2:numMons
    for f in filter(x -> startswith(x, pvpokeRanks[i]["speciesName"]), readdir())
        if(!(f in filter(x -> startswith(x, pvpokeRanks[i]["speciesName"] * " (Alolan)"), readdir())))
            battles = CSV.read(f; delim=',');
            deletecols!(battles, 3:4)
            deletecols!(battles, 1)
            rankings = hcat(rankings, battles, makeunique = true)
            rename!(rankings, Symbol("Battle Rating")=>Symbol(pvpokeRanks[i]["speciesName"]))
        end
    end
end

iterator = 1

for i = 1:length(pvpokeRanks)
    delete = true
    for j = 1:numMons
        if startswith(rankings[iterator, 1], pvpokeRanks[j]["speciesName"])
            delete = false
        end
    end
    if delete == true
        deleterows!(rankings, iterator)
        iterator -= 1
    end
    iterator += 1
end

names = Array{String}(undef, numMons, 1)
for i = 1:numMons
    names[i, 1] = pvpokeRanks[i]["speciesName"]
end

rank = Array{Int64}(undef, numMons, 1)

for i = 1:numMons
    rank[i, 1] = i
end

rank = hcat(names, rank)

alphabeticalRanks = sortslices(rank, by=x->x[1], dims = 1, rev = false)

rankings = hcat( alphabeticalRanks[:, 2], rankings)

rankings = sort!(rankings)

deletecols!(rankings, 1)

rankings

45×46 DataFrame. Omitted printing of 41 columns
│ Row │ Pokemon             │ Venusaur │ Dragonair │ Meganium │ Charizard │
│     │ String⍰             │ Int64⍰   │ Int64⍰    │ Int64⍰   │ Int64⍰    │
├─────┼─────────────────────┼──────────┼───────────┼──────────┼───────────┤
│ 1   │ Venusaur VW+FP/SB   │ 500      │ 577       │ 227      │ 900       │
│ 2   │ Dragonair DB+AT/R   │ 422      │ 500       │ 534      │ 437       │
│ 3   │ Meganium VW+FP/E    │ 772      │ 465       │ 500      │ 745       │
│ 4   │ Charizard FS+BB/DC  │ 99       │ 562       │ 254      │ 500       │
│ 5   │ Swampert MS+HC/E    │ 686      │ 367       │ 759      │ 140       │
│ 6   │ Kingdra DB+O/HP     │ 589      │ 482       │ 709      │ 356       │
│ 7   │ Lapras IS+S/SB      │ 267      │ 428       │ 591      │ 309       │
│ 8   │ Venomoth C+SW/PF    │ 277      │ 550       │ 440      │ 715       │
│ 9   │ Haunter SC+SP/SB    │ 500      │ 500       │ 500      │ 341       │
│ 10  │ Ivysaur VW+PW/SB    │ 589      │ 844       │ 226      │ 900       │
⋮
│ 35  │ Dustox C+SW/SB      │ 238      │ 503       │ 481      │ 762       │
│ 36  │ Sudowoodo C+RS/E    │ 800      │ 693       │ 767      │ 300       │
│ 37  │ Ninetales FS+F/P    │ 408      │ 821       │ 337      │ 521       │
│ 38  │ Sealeo PS+BS/AB     │ 500      │ 286       │ 500      │ 616       │
│ 39  │ Weepinbell RL+SB/SB │ 691      │ 593       │ 675      │ 758       │
│ 40  │ Spiritomb SP+SB/OW  │ 585      │ 573       │ 675      │ 547       │
│ 41  │ Grotle RL+BS/R      │ 800      │ 647       │ 519      │ 788       │
│ 42  │ Cradily I+GK/SE     │ 508      │ 507       │ 526      │ 918       │
│ 43  │ Lanturn WG+T/HP     │ 792      │ 538       │ 805      │ 329       │
│ 44  │ Houndoom S+C/F      │ 565      │ 554       │ 405      │ 410       │
│ 45  │ Relicanth WG+AT/AP  │ 800      │ 511       │ 812      │ 191       │

### Colors

Just defining some colors so that things look pretty. However, there aren't cup typings this time, so its fairly arbitrary as to which typing I choose to determine the color of each mon. For Alolan Ninetales, for instance, I think of ice first, and thus that is the color of Alolan Ninetales in this model. Feel free to change these around as you feel, but given that they are primarily an aesthetic choice, I elected to not put a whole lot of thought into which color each mon gets.

In [60]:
opacity = 0.7
grass = RGBA(94/255,189/255,91/255, opacity); dragon = RGBA(14/255,104/255,184/255, opacity); dark = RGBA(86/255,86/255,99/255, opacity); normal = RGBA(153/255,159/255,161/255, opacity); fire = RGBA(254/255,163/255,84/255, opacity); ground = RGBA(212/255,141/255,91/255, opacity); poison = RGBA(193/255,98/255,212/255, opacity); rock = RGBA(208/255,196/255,142/255, opacity); ghost = RGBA(89/255,107/255,181/255, opacity); psychic = RGBA(245/255,126/255,121/255, opacity); ice = RGBA(120/255,212/255,192/255, opacity); water = RGBA(86/255,158/255,222/255, opacity); fighting = RGBA(213/255,63/255,91/255, opacity); steel = RGBA(82/255,142/255,160/255, opacity); fairy = RGBA(240/255,152/255,228/255, opacity); flying = RGBA(148/255,171/255,225/255, opacity); bug = RGBA(158/255,195/255,49/255, opacity); electric = RGBA(246/255,215/255,75/255, opacity);

### Restrictions

Here I am adding a function to see if a particular three mon team is restricted, that is, if it contains more than one starter.

In [61]:
const limitedMons = ["Bulbasaur" "Ivysaur" "Venusaur" "Charmander" "Charmeleon" "Charizard" "Squirtle" "Warturtle" "Blastoise"
                    "Chikorita" "Bayleef" "Meganium" "Cyndaquil" "Quilava" "Typhlosion" "Totodile" "Croconaw" "Feraligatr"
                    "Treecko" "Grovyle" "Sceptile" "Torchic" "Combusken" "Blaziken" "Mudkip" "Marshtomp" "Swampert"
                    "Turtwig" "Grotle" "Torterra" "Chimchar" "Monferno" "Infernape" "Piplup" "Prinplup" "Empoleon"]
function isRestricted(mon1, mon2, mon3)
    numLimited = 0
    if in(pvpokeRanks[mon1]["speciesName"], limitedMons)
        numLimited += 1 
    end
    if in(pvpokeRanks[mon2]["speciesName"], limitedMons)
        numLimited += 1
        if numLimited > 1
            return true
        end
    end
    if in(pvpokeRanks[mon3]["speciesName"], limitedMons)
        numLimited += 1
        if numLimited > 1
            return true
        end
    end
    return false
end

isRestricted (generic function with 1 method)

### Team Numbers

Here I'm mapping the 3 mon teams to a number, such that each team has its own unique number from 1 to 12180 ($\frac{30 \cdot 29 \cdot 28}{2}$)

In [62]:
teamNumberVar = zeros(numMons, numMons, numMons)
i = 1
for mon1 = 1:numMons , mon2 = 1:(numMons - 1) , mon3 = (mon2 + 1):numMons
    if mon1 != mon2 && mon1 != mon3 && !isRestricted(mon1, mon2, mon3)
        teamNumberVar[mon1, mon2, mon3] = Int(i)
        i += 1
    end
end
const teamNumber = teamNumberVar;
const numTeams = i - 1;
numTeams

36465

### Setting Up the Tables

I'm grabbing just the data I need and putting it in a constant (for SPEED) matrix, and also defining a matrix to store the outputs in.

In [63]:
# clean up ranking data for simulation
# Defining as constant for SPEED
const ranks = [rankings[i, j] for i = 1:numMons, j = 2:(numMons + 1)];
teamBattles = zeros(numTeams, numTeams);
#teamBattlesWeighted = zeros(numTeams, numTeams);

## The Model

### Assumptions

So, we all know assumptions are bad. But in data science, sometimes our models need to be simplified so we can work with the information that we have in a reasonable time scale. Therefore, I have made some simplifying assumptions for the model of PvP battles, and will add some uncertainty to account for some of the differences between this model and the reality of PvP battling.

*   **No Switching:** Switching is a weird mechanic for which the timing is never consistent, when and if you should use it in scenario X is hotly debated, and then your opponent switches, which is a lot of variability. As will be a pretty common motivator among all of these reasons, if I have the home team switch perfectly, it involves some knowledge of the opposing team that you don't have in that situation. All of this to say, for this model, nobody switches because it makes everything work better, my life easier, and doesn't run the risk of having the model make decisions better than any player could be expected to. 

*   **Each Mon Gets One Shield:** I know, I know. Doesn't that add up to three shields? Well, yeah. But again, shielding choices add in some variability, and perfect use involves some knowledge of the opposing team that you don't have in that situation. Plus, then one data set is needed, the 1-1 shield matchups from PvPoke, which I believe also implicitly have the shield used on the first charged move. 

*   **Players Play Perfectly Otherwise:** Whoa. In all that avoidance of perfection, now I want my model to be perfect? Well, for one, this is just based on the assumptions in PvPoke. For two, I stand by that decision, as its perfection that's acheivable by the knowledge a player has in a particular situation. You may not know when to shield or switch, but you do probably know that you want an excellent charged move and to tap out fast moves (also I'm assuming everyone is on 1.57 or higher, because I do not want to deal with under or overtapping). Also, this model assumes the ideal moveset for each mon (though you can change that by changing the CSVs.

*   **Putting a Mon in the Second Position is the Same as Putting it in the Third:** I think this assumption is generally accurate. I think I've seen arguments for putting the fast switch in the third position, but I'm also assuming players play perfectly and there's no switching, so I genuinely think this doesn't affect the model, but I'm including it anyway.

*   **Mons Appear Uniformly Among the Top 30 Mons:** Sorry, Spoink fans. This is to keep the amount of data this processes to a reasonable amount. There is another version of this model that uses the Silph distribution instead, however, Silph data does not exist for the Ferocious Cup yet.

*   **Score Above 1500 is a Win:** This is based on the PvPoke battle score, and since there are three battles, its out of 3000 instead of 1000. Scoring is explained more below, but this is the assumption of what we do with that score. 

None of these assumptions are set in stone. In fact, if you have a way to change them and think that that's more useful to you, 1) go ahead and 2) let me know how you did it. 

### Scoring

I know, this section is already too long, just show you the data. But here's what the data means. Each PvPoke battle is given a score of 0-1000 with 500 representing a tie, and above that being a win, below that a loss. The score for the three-mon battle is adding those three scores together. But, that depends on which matchups you see. The lead pokemon always face each other. If your lead wins, you get the favorable matchups (because your opponent had to put in a pokemon and you can counter it), if your lead loses, you get the less favorable matchups. And, as stated above, over 1500 is a win.

In [64]:
function individual_battle_verbose(home1,home2,home3,away1,away2,away3,rankings)
    
                 score  = rankings[away1, home1]
    secondBattleResult1 = rankings[away2, home2]
    secondBattleResult2 = rankings[away3, home2]
    thirdBattleResult1  = rankings[away2, home3]
    thirdBattleResult2  = rankings[away3, home3]

    if score > 500 
        score += max(secondBattleResult2 + thirdBattleResult1, secondBattleResult1 + thirdBattleResult2) 
    elseif score < 500 
        score += min(secondBattleResult2 + thirdBattleResult1, secondBattleResult1 + thirdBattleResult2) 
    else
        score += (secondBattleResult2 + thirdBattleResult1 + secondBattleResult1 + thirdBattleResult2)/2.0 
    end 
    
    return score
    
end;

### Testing

The timing stuff is mostly for me, to make sure things can run in a reasonable time. But they exist and they're here in case you're curious

In [65]:
# Run once to compile, run again to test speed (with different input so no cheating)
individual_battle_verbose(1,2,3,4,5,6,ranks)
@time score = individual_battle_verbose(1,2,7,4,5,6,ranks)

  0.000002 seconds (6 allocations: 224 bytes)


1054

### Testing a Team

This function does all possible teams against a certain team. And there are two versions, depending on if you want verbose output.

In [66]:
function run_away_teams_verbose(home1,home2,home3,ranks)

    for away1 = 1:numMons , away2 = 1:(numMons - 1) , away3 = (away2 + 1):numMons

        if away1 != away2 && away1 != away3 && !isRestricted(away1, away2, away3)

            # Do the battle!
            # Use the function we wrote above
            score = individual_battle_verbose(home1,home2,home3,away1,away2,away3,ranks)
            teamBattles[Int(teamNumber[home1,home2,home3]), Int(teamNumber[away1,away2,away3])] = score
        end
    end
end;

In [67]:
# Run once to compile, run again to test speed (with different input so no cheating)
run_away_teams_verbose(1,2,6,ranks)
@time run_away_teams_verbose(1,2,7,ranks)

  0.024828 seconds (72.42 k allocations: 1.105 MiB)


In [68]:
function run_home_teams_verbose(ranks)
    
    for home1 = 1:numMons , home2 = 1:(numMons - 1) , home3 = (home2 + 1):numMons 
        if home1 != home2 && home1 != home3 && !isRestricted(home1, home2, home3)
            run_away_teams_verbose(home1,home2,home3,ranks)
        end 
    end 
end;

In [69]:
# Run once to compile, run again to test speed 
run_home_teams_verbose(ranks)
@time run_home_teams_verbose(ranks);

849.859227 seconds (3.95 G allocations: 58.865 GiB, 0.79% gc time)


In [70]:
teamBattles

36465×36465 Array{Float64,2}:
 1499.5  1428.0  1515.5  1638.5  1568.5  …  2268.0  1885.0  2128.0  2159.0
 1570.5  1495.0  1577.0  1471.5  1662.0     2060.0  1898.0  1920.0  1951.0
 1483.0  1421.5  1499.5  1627.0  1553.5     2127.0  1838.0  1854.0  1823.0
 1360.5  1527.5  1372.0  1500.0  1752.0     1878.0  2251.0  2267.0  1981.0
 1430.0  1336.5  1445.0  1247.0  1499.5     2023.0  1853.0  1869.0  1888.0
 1467.0  1360.5  1495.0  1514.0  1548.0  …  2031.0  1988.0  1891.0  2035.0
 1549.5  1388.0  1581.5  1367.0  1738.5     1895.0  2231.0  2247.0  1732.0
 1611.0  1460.5  1660.5  1604.5  1705.5     2042.0  1890.0  1906.0  1899.0
 1396.0  1321.5  1472.0  1587.0  1716.0     2296.0  2171.0  2187.0  2187.0
 1235.5  1343.5  1470.0  1379.5  1479.0     2102.0  1686.0  1751.0  1782.0
 1549.0  1474.0  1521.0  1484.0  1622.0  …  2081.0  1934.0  1950.0  1798.0
 1455.0  1541.5  1513.0  1490.0  1562.0     1904.0  2228.0  2244.0  2007.0
 1569.5  1448.5  1675.5  1624.5  1721.0     2340.0  2045.0  2200.0  22

### Summary Stats

Here I'm going to save the summary stats for every team, where my summary stats are the number of wins, and the mean, variance, skewness, and kurtosis of the scores. 

In [71]:
summaryStats = zeros(numTeams, 8)
i = 1
p = x -> (x > 1500.0)
for mon1 = 1:numMons , mon2 = 1:(numMons - 1) , mon3 = (mon2 + 1):numMons
    if mon1 != mon2 && mon1 != mon3 && !isRestricted(mon1, mon2, mon3)
        team = teamBattles[Int(teamNumber[Int(mon1), Int(mon2), Int(mon3)]),:]
        numWins = count(p,team)
        summaryStats[i, :] = [numWins mean(team) var(team) skewness(team) kurtosis(team) mon1 mon2 mon3]
        i += 1
    end
end        

## Number of Wins

Here we've got the information related to the number of wins. Below is a histogram of the number of teams vs their number of wins, a sorted list that shows the best and worst teams by number of wins, and a histogram comparing the scores of the best and worst teams by number of wins.

In [113]:
histogram(summaryStats[:, 1], label = "Number of Wins")

In [73]:
sumStatsNumWins = sortslices(summaryStats, by=x->x[1], dims = 1, rev = true)

for i = 1:numTeams
    sumStatsNumWins[i, 1] /= (numTeams / 100.0)
end

names1 = Array{String}(undef, numTeams, 1)
for i = 1:numTeams
    names1[i, 1] = pvpokeRanks[Int(sumStatsNumWins[i, 6])]["speciesName"]
end

names2 = Array{String}(undef, numTeams, 1)
for i = 1:numTeams
    names2[i, 1] = pvpokeRanks[Int(sumStatsNumWins[i, 7])]["speciesName"]
end

names3 = Array{String}(undef, numTeams, 1)
for i = 1:numTeams
    names3[i, 1] = pvpokeRanks[Int(sumStatsNumWins[i, 8])]["speciesName"]
end

sumStatsNumWins = hcat(sumStatsNumWins, names1)
sumStatsNumWins = hcat(sumStatsNumWins, names2)
sumStatsNumWins = hcat(sumStatsNumWins, names3)

sumStatsNumWins = DataFrame(sumStatsNumWins)

rename!(sumStatsNumWins, Symbol("x1")=>Symbol("Win %"))
rename!(sumStatsNumWins, Symbol("x2")=>Symbol("Avg Score"))
rename!(sumStatsNumWins, Symbol("x3")=>Symbol("Avg Variance"))
rename!(sumStatsNumWins, Symbol("x4")=>Symbol("Avg Skew"))
rename!(sumStatsNumWins, Symbol("x5")=>Symbol("Avg Kurt"))
rename!(sumStatsNumWins, Symbol("x6")=>Symbol("Rank Mon 1"))
rename!(sumStatsNumWins, Symbol("x7")=>Symbol("Rank Mon 2"))
rename!(sumStatsNumWins, Symbol("x8")=>Symbol("Rank Mon 3"))
rename!(sumStatsNumWins, Symbol("x9")=>Symbol("Mon 1"))
rename!(sumStatsNumWins, Symbol("x10")=>Symbol("Mon 2"))
rename!(sumStatsNumWins, Symbol("x11")=>Symbol("Mon 3"))

36465×11 DataFrame. Omitted printing of 6 columns
│ Row   │ Win %   │ Avg Score │ Avg Variance │ Avg Skew  │ Avg Kurt   │
│       │ Any     │ Any       │ Any          │ Any       │ Any        │
├───────┼─────────┼───────────┼──────────────┼───────────┼────────────┤
│ 1     │ 76.8929 │ 1719.06   │ 1.10096e5    │ -0.450756 │ 0.149497   │
│ 2     │ 76.7366 │ 1695.06   │ 70375.8      │ -0.27595  │ -0.20201   │
│ 3     │ 76.6159 │ 1725.05   │ 99749.6      │ -0.51737  │ -0.0458774 │
│ 4     │ 76.3691 │ 1721.88   │ 97283.7      │ -0.340948 │ -0.269123  │
│ 5     │ 76.339  │ 1691.12   │ 85885.9      │ -0.544382 │ 0.192334   │
│ 6     │ 76.2128 │ 1694.64   │ 99462.7      │ -0.504259 │ 0.304305   │
│ 7     │ 76.0071 │ 1674.63   │ 75719.8      │ -0.245434 │ 0.117152   │
│ 8     │ 75.9962 │ 1707.33   │ 1.08209e5    │ -0.601585 │ 0.122403   │
│ 9     │ 75.9002 │ 1731.45   │ 1.09189e5    │ -0.426449 │ -0.148006  │
│ 10    │ 75.8618 │ 1722.34   │ 112346.0     │ -0.330152 │ -0.0192731 │
⋮
│ 36455 │ 25.4628 │ 1254.88   │ 1.43754e5    │ 0.516275  │ -0.409337  │
│ 36456 │ 25.4545 │ 1283.38   │ 1.22723e5    │ 0.643909  │ -0.26697   │
│ 36457 │ 25.2269 │ 1287.5    │ 1.07812e5    │ 0.513478  │ -0.307431  │
│ 36458 │ 25.2022 │ 1269.84   │ 1.31053e5    │ 0.547036  │ -0.237917  │
│ 36459 │ 24.8841 │ 1233.63   │ 1.46085e5    │ 0.363328  │ -0.503556  │
│ 36460 │ 24.7031 │ 1269.79   │ 118295.0     │ 0.478888  │ -0.302747  │
│ 36461 │ 24.3028 │ 1278.45   │ 1.16723e5    │ 0.653128  │ -0.198246  │
│ 36462 │ 23.6446 │ 1259.23   │ 1.25734e5    │ 0.616424  │ -0.134783  │
│ 36463 │ 23.6309 │ 1230.76   │ 1.41936e5    │ 0.349697  │ -0.363731  │
│ 36464 │ 23.4252 │ 1228.99   │ 1.43042e5    │ 0.581175  │ -0.287194  │
│ 36465 │ 23.1866 │ 1225.75   │ 1.37977e5    │ 0.432921  │ -0.348104  │

In [74]:
histogram(teamBattles[Int(teamNumber[Int(sumStatsNumWins[1, 6]), Int(sumStatsNumWins[1, 7]), Int(sumStatsNumWins[1, 8])]),:], bins = 100, color = dragon, label = "#1 " * sumStatsNumWins[1, 9] * ", " * sumStatsNumWins[1, 10] * ", " * sumStatsNumWins[1, 11])
histogram!(teamBattles[Int(teamNumber[Int(sumStatsNumWins[numTeams, 6]), Int(sumStatsNumWins[numTeams, 7]), Int(sumStatsNumWins[numTeams, 8])]),:], bins = 100, color = poison, label = "#12180 " * sumStatsNumWins[numTeams, 9] * ", " * sumStatsNumWins[numTeams, 10] * ", " * sumStatsNumWins[numTeams, 11])
vline!([1500], color = :red, label = "W/L Cutoff")

Here we've got the number of wins on average in every team a particular pokemon is a part of and rank them below, again showing the best and worst.

In [75]:
avgNumOfWins = zeros(numMons, 2)
i = 1
for mon1 = 1:numMons , mon2 = 1:(numMons - 1) , mon3 = (mon2 + 1):numMons
    if mon1 != mon2 && mon1 != mon3 && !isRestricted(mon1, mon2, mon3)
        avgNumOfWins[mon1, 1] += summaryStats[i, 1]
        avgNumOfWins[mon2, 1] += summaryStats[i, 1]
        avgNumOfWins[mon3, 1] += summaryStats[i, 1]
        i += 1
    end
end
for i = 1:numMons
    avgNumOfWins[i, 2] = i
    divisor = 0.0
    for mon2 = 1:numMons, mon3 = mon2 + 1:numMons
        if(teamNumber[i, mon2, mon3] > 0)
           divisor += 1.0
        end
        if(teamNumber[mon2, i, mon3] > 0)
           divisor += 1.0
        end
        if(teamNumber[mon2, mon3, i] > 0)
           divisor += 1.0
        end
    end
    avgNumOfWins[i, 1] /= (divisor * numTeams / 100.0)
end

avgNumOfWinsSorted = sortslices(avgNumOfWins, by=x->x[1], dims = 1, rev = true)

nameNumWins = Array{String}(undef, numMons, 1)
for i = 1:numMons
    nameNumWins[i, 1] = pvpokeRanks[Int(avgNumOfWinsSorted[i, 2])]["speciesName"]
end

avgNumOfWinsSorted = hcat(avgNumOfWinsSorted, nameNumWins)

avgNumOfWinsSorted = DataFrame(avgNumOfWinsSorted)

rename!(avgNumOfWinsSorted, Symbol("x1")=>Symbol("Win %"))
rename!(avgNumOfWinsSorted, Symbol("x2")=>Symbol("Rank"))
rename!(avgNumOfWinsSorted, Symbol("x3")=>Symbol("Name"))

45×3 DataFrame
│ Row │ Win %   │ Rank │ Name             │
│     │ Any     │ Any  │ Any              │
├─────┼─────────┼──────┼──────────────────┤
│ 1   │ 88.025  │ 2.0  │ Dragonair        │
│ 2   │ 86.7887 │ 5.0  │ Swampert         │
│ 3   │ 84.3974 │ 22.0 │ Whiscash         │
│ 4   │ 84.0604 │ 20.0 │ Banette          │
│ 5   │ 83.2874 │ 7.0  │ Lapras           │
│ 6   │ 82.7434 │ 30.0 │ Politoed         │
│ 7   │ 81.0811 │ 45.0 │ Relicanth        │
│ 8   │ 80.5495 │ 4.0  │ Charizard        │
│ 9   │ 80.0922 │ 32.0 │ Castform (Rainy) │
│ 10  │ 78.9624 │ 17.0 │ Flygon           │
⋮
│ 35  │ 70.8785 │ 23.0 │ Torkoal          │
│ 36  │ 70.7367 │ 41.0 │ Grotle           │
│ 37  │ 70.359  │ 31.0 │ Sceptile         │
│ 38  │ 69.6344 │ 28.0 │ Charmeleon       │
│ 39  │ 69.3077 │ 42.0 │ Cradily          │
│ 40  │ 68.7171 │ 14.0 │ Froslass         │
│ 41  │ 66.4361 │ 26.0 │ Piloswine        │
│ 42  │ 65.9293 │ 33.0 │ Beedrill         │
│ 43  │ 64.298  │ 10.0 │ Ivysaur          │
│ 44  │ 61.4869 │ 35.0 │ Dustox           │
│ 45  │ 59.9512 │ 34.0 │ Wormadam (Plant) │

Here I've plotted the PvPoke ranking compared to the average number of wins. I think its not necessarily a surprise that there's not a perfect correlation here (you don't put in the top 6 ranked mons generally), but there is a pretty clear negative slope here. The big spike I think is Lickilicky.

In [76]:
plot(1:numMons, avgNumOfWins[:, 1], label = "Average Number of Wins")

In [77]:
histogram(teamBattles[Int(teamNumber[1, 2, 6]),:], bins = 100, color = grass, label = "#1 PvPoke Venusaur, Dragonair, Kingdra")
histogram!(teamBattles[Int(teamNumber[Int(sumStatsNumWins[1, 6]), Int(sumStatsNumWins[1, 7]), Int(sumStatsNumWins[1, 8])]),:], bins = 100, color = dragon, label = "#1 Team Model " * sumStatsNumWins[1, 9] * ", " * sumStatsNumWins[1, 10] * ", " * sumStatsNumWins[1, 11])

## Average Score

Here we've got the information related to the average. Below is a histogram of the number of teams vs their average, a sorted list that shows the best and worst teams by average score, and a histogram comparing the scores of the best and worst teams by average score. Not that there are minor differences between the average score statistics and the number of wins. I generally consider number of wins to be a more useful statistic (as it doesn't necessarily matter to me how much I win by as long as I win), but I could see arguments for using this particular statistic instead.

In [78]:
histogram(summaryStats[:, 2], label = "Mean Score")

In [79]:
sumStatsAvgScore = sortslices(summaryStats, by=x->x[2], dims = 1, rev = true)

names1 = Array{String}(undef, numTeams, 1)
for i = 1:numTeams
    names1[i, 1] = pvpokeRanks[Int(sumStatsAvgScore[i, 6])]["speciesName"]
end

names2 = Array{String}(undef, numTeams, 1)
for i = 1:numTeams
    names2[i, 1] = pvpokeRanks[Int(sumStatsAvgScore[i, 7])]["speciesName"]
end

names3 = Array{String}(undef, numTeams, 1)
for i = 1:numTeams
    names3[i, 1] = pvpokeRanks[Int(sumStatsAvgScore[i, 8])]["speciesName"]
end

sumStatsAvgScore = hcat(sumStatsAvgScore, names1)
sumStatsAvgScore = hcat(sumStatsAvgScore, names2)
sumStatsAvgScore = hcat(sumStatsAvgScore, names3)

sumStatsAvgScore = DataFrame(sumStatsAvgScore)

rename!(sumStatsAvgScore, Symbol("x1")=>Symbol("Num of Wins"))
rename!(sumStatsAvgScore, Symbol("x2")=>Symbol("Avg Score"))
rename!(sumStatsAvgScore, Symbol("x3")=>Symbol("Avg Variance"))
rename!(sumStatsAvgScore, Symbol("x4")=>Symbol("Avg Skew"))
rename!(sumStatsAvgScore, Symbol("x5")=>Symbol("Avg Kurt"))
rename!(sumStatsAvgScore, Symbol("x6")=>Symbol("Rank Mon 1"))
rename!(sumStatsAvgScore, Symbol("x7")=>Symbol("Rank Mon 2"))
rename!(sumStatsAvgScore, Symbol("x8")=>Symbol("Rank Mon 3"))
rename!(sumStatsAvgScore, Symbol("x9")=>Symbol("Mon 1"))
rename!(sumStatsAvgScore, Symbol("x10")=>Symbol("Mon 2"))
rename!(sumStatsAvgScore, Symbol("x11")=>Symbol("Mon 3"))

36465×11 DataFrame. Omitted printing of 6 columns
│ Row   │ Num of Wins │ Avg Score │ Avg Variance │ Avg Skew  │ Avg Kurt    │
│       │ Any         │ Any       │ Any          │ Any       │ Any         │
├───────┼─────────────┼───────────┼──────────────┼───────────┼─────────────┤
│ 1     │ 27118.0     │ 1732.65   │ 1.38958e5    │ -0.339139 │ -0.165235   │
│ 2     │ 27677.0     │ 1731.45   │ 1.09189e5    │ -0.426449 │ -0.148006   │
│ 3     │ 27496.0     │ 1731.44   │ 1.13897e5    │ -0.224031 │ -0.396699   │
│ 4     │ 27565.0     │ 1730.81   │ 1.16861e5    │ -0.499086 │ -0.00806153 │
│ 5     │ 27364.0     │ 1730.03   │ 1.34687e5    │ -0.397882 │ -0.0778172  │
│ 6     │ 26942.0     │ 1728.78   │ 1.39674e5    │ -0.328795 │ -0.189155   │
│ 7     │ 27938.0     │ 1725.05   │ 99749.6      │ -0.51737  │ -0.0458774  │
│ 8     │ 27663.0     │ 1722.34   │ 112346.0     │ -0.330152 │ -0.0192731  │
│ 9     │ 27848.0     │ 1721.88   │ 97283.7      │ -0.340948 │ -0.269123   │
│ 10    │ 27170.0     │ 1720.22   │ 1.16561e5    │ -0.425948 │ -0.145733   │
⋮
│ 36455 │ 10483.0     │ 1254.14   │ 1.55114e5    │ 0.262234  │ -0.669824   │
│ 36456 │ 9730.0      │ 1249.61   │ 151297.0     │ 0.352984  │ -0.610944   │
│ 36457 │ 10687.0     │ 1249.51   │ 1.72574e5    │ 0.422644  │ -0.723924   │
│ 36458 │ 9669.0      │ 1248.01   │ 1.57827e5    │ 0.569998  │ -0.480698   │
│ 36459 │ 10848.0     │ 1244.47   │ 1.7875e5     │ 0.286251  │ -0.835726   │
│ 36460 │ 9837.0      │ 1243.07   │ 151926.0     │ 0.386053  │ -0.619914   │
│ 36461 │ 9481.0      │ 1241.2    │ 1.49641e5    │ 0.582789  │ -0.491137   │
│ 36462 │ 9074.0      │ 1233.63   │ 1.46085e5    │ 0.363328  │ -0.503556   │
│ 36463 │ 8617.0      │ 1230.76   │ 1.41936e5    │ 0.349697  │ -0.363731   │
│ 36464 │ 8542.0      │ 1228.99   │ 1.43042e5    │ 0.581175  │ -0.287194   │
│ 36465 │ 8455.0      │ 1225.75   │ 1.37977e5    │ 0.432921  │ -0.348104   │

In [80]:
histogram(teamBattles[Int(teamNumber[Int(sumStatsAvgScore[1, 6]), Int(sumStatsAvgScore[1, 7]), Int(sumStatsAvgScore[1, 8])]),:], bins = 100, color = dragon, label = "#1 " * sumStatsAvgScore[1, 9] * ", " * sumStatsAvgScore[1, 10] * ", " * sumStatsAvgScore[1, 11])
histogram!(teamBattles[Int(teamNumber[Int(sumStatsAvgScore[numTeams, 6]), Int(sumStatsAvgScore[numTeams, 7]), Int(sumStatsAvgScore[numTeams, 8])]),:], bins = 100, color = poison, label = "#12180 " * sumStatsAvgScore[numTeams, 9] * ", " * sumStatsAvgScore[numTeams, 10] * ", " * sumStatsAvgScore[numTeams, 11])
vline!([1500], color = :red, label = "W/L Cutoff")

In [81]:
avgScore = zeros(numMons, 2)
i = 1
for mon1 = 1:numMons , mon2 = 1:(numMons - 1) , mon3 = (mon2 + 1):numMons
    if mon1 != mon2 && mon1 != mon3 && !isRestricted(mon1, mon2, mon3)
        avgScore[mon1, 1] += summaryStats[i, 2]
        avgScore[mon2, 1] += summaryStats[i, 2]
        avgScore[mon3, 1] += summaryStats[i, 2]
        i += 1
    end
end
for i = 1:numMons
    avgScore[i, 2] = i
    divisor = 0.0
    for mon2 = 1:numMons, mon3 = mon2 + 1:numMons
        if(teamNumber[i, mon2, mon3] > 0)
           divisor += 1.0
        end
        if(teamNumber[mon2, i, mon3] > 0)
           divisor += 1.0
        end
        if(teamNumber[mon2, mon3, i] > 0)
           divisor += 1.0
        end
    end
    avgScore[i, 1] /= (divisor * numTeams)
end
#avgScore[:, 1] ./ (numTeams / (numMons / 3.0))

avgScoreSorted = sortslices(avgScore, by=x->x[1], dims = 1, rev = true)

nameAvgScore = Array{String}(undef, numMons, 1)
for i = 1:numMons
    nameAvgScore[i, 1] = pvpokeRanks[Int(avgScoreSorted[i, 2])]["speciesName"]
end

avgScoreSorted = hcat(avgScoreSorted, nameAvgScore)

avgScoreSorted = DataFrame(avgScoreSorted)

rename!(avgScoreSorted, Symbol("x1")=>Symbol("Avg Score"))
rename!(avgScoreSorted, Symbol("x2")=>Symbol("Rank"))
rename!(avgScoreSorted, Symbol("x3")=>Symbol("Name"))

45×3 DataFrame
│ Row │ Avg Score │ Rank │ Name             │
│     │ Any       │ Any  │ Any              │
├─────┼───────────┼──────┼──────────────────┤
│ 1   │ 0.0648478 │ 2.0  │ Dragonair        │
│ 2   │ 0.0647382 │ 5.0  │ Swampert         │
│ 3   │ 0.0640972 │ 20.0 │ Banette          │
│ 4   │ 0.0637777 │ 22.0 │ Whiscash         │
│ 5   │ 0.0637718 │ 7.0  │ Lapras           │
│ 6   │ 0.0635999 │ 4.0  │ Charizard        │
│ 7   │ 0.0634683 │ 17.0 │ Flygon           │
│ 8   │ 0.0634107 │ 30.0 │ Politoed         │
│ 9   │ 0.0632247 │ 45.0 │ Relicanth        │
│ 10  │ 0.0628224 │ 9.0  │ Haunter          │
⋮
│ 35  │ 0.0608751 │ 19.0 │ Muk              │
│ 36  │ 0.0608051 │ 31.0 │ Sceptile         │
│ 37  │ 0.0606141 │ 28.0 │ Charmeleon       │
│ 38  │ 0.0602287 │ 14.0 │ Froslass         │
│ 39  │ 0.0597958 │ 33.0 │ Beedrill         │
│ 40  │ 0.0597937 │ 23.0 │ Torkoal          │
│ 41  │ 0.0594599 │ 26.0 │ Piloswine        │
│ 42  │ 0.0594032 │ 42.0 │ Cradily          │
│ 43  │ 0.0585205 │ 10.0 │ Ivysaur          │
│ 44  │ 0.0584379 │ 35.0 │ Dustox           │
│ 45  │ 0.0575606 │ 34.0 │ Wormadam (Plant) │

Again, there isn't a strong correlation with the average score to the PvPoke ranking, but that is to be expected. Also, average score is strongly correlated with the number of wins, which is also to be expected. So this particular statistic is not the same as number of wins, or even leads to the same conclusion, but they are correlated.

In [82]:
plot(1:numMons, avgScore[:, 1], label = "Average Score")

In [83]:
plot(avgScore[:, 1], avgNumOfWins[:, 1], seriestype=:scatter, label = "Average Score vs. Num of Wins")

## Variance

Here's where the team decision making from this data begins to be less obvious. If you're not interested in Variance, Skewness or Kurtosis, I encourage you to scroll down past these sections. I do include these sections on higher order moments in part because I find them interesting, but also these might be useful for someone somewhere, and as such, I included them. 

Variance is a measure of how wide (or thin) the distribution is. Teams with a higher variance have scores that are more spread out, while teams with lower variance have scores that stay closer to their mean value. This is independent of the mean (as this variance is a centered moment), and thus one team is not necessarily better than the other by this metric, just more or less spread out.

In [84]:
histogram(summaryStats[:, 3], label = "Variance")

In [85]:
sumStatsVariance = sortslices(summaryStats, by=x->x[3], dims = 1, rev = true)

names1 = Array{String}(undef, numTeams, 1)
for i = 1:numTeams
    names1[i, 1] = pvpokeRanks[Int(sumStatsVariance[i, 6])]["speciesName"]
end

names2 = Array{String}(undef, numTeams, 1)
for i = 1:numTeams
    names2[i, 1] = pvpokeRanks[Int(sumStatsVariance[i, 7])]["speciesName"]
end

names3 = Array{String}(undef, numTeams, 1)
for i = 1:numTeams
    names3[i, 1] = pvpokeRanks[Int(sumStatsVariance[i, 8])]["speciesName"]
end

sumStatsVariance = hcat(sumStatsVariance, names1)
sumStatsVariance = hcat(sumStatsVariance, names2)
sumStatsVariance = hcat(sumStatsVariance, names3)

sumStatsVariance = DataFrame(sumStatsVariance)

rename!(sumStatsVariance, Symbol("x1")=>Symbol("Num of Wins")); rename!(sumStatsVariance, Symbol("x2")=>Symbol("Avg Score")); rename!(sumStatsVariance, Symbol("x3")=>Symbol("Avg Variance")); rename!(sumStatsVariance, Symbol("x4")=>Symbol("Avg Skew")); rename!(sumStatsVariance, Symbol("x5")=>Symbol("Avg Kurt")); rename!(sumStatsVariance, Symbol("x6")=>Symbol("Rank Mon 1")); rename!(sumStatsVariance, Symbol("x7")=>Symbol("Rank Mon 2")); rename!(sumStatsVariance, Symbol("x8")=>Symbol("Rank Mon 3")); rename!(sumStatsVariance, Symbol("x9")=>Symbol("Mon 1")); rename!(sumStatsVariance, Symbol("x10")=>Symbol("Mon 2")); rename!(sumStatsVariance, Symbol("x11")=>Symbol("Mon 3"))

36465×11 DataFrame. Omitted printing of 6 columns
│ Row   │ Num of Wins │ Avg Score │ Avg Variance │ Avg Skew   │ Avg Kurt   │
│       │ Any         │ Any       │ Any          │ Any        │ Any        │
├───────┼─────────────┼───────────┼──────────────┼────────────┼────────────┤
│ 1     │ 16598.0     │ 1501.06   │ 2.56292e5    │ 0.220853   │ -1.04732   │
│ 2     │ 20826.0     │ 1570.16   │ 2.55724e5    │ -0.120186  │ -1.05575   │
│ 3     │ 16530.0     │ 1498.74   │ 2.54756e5    │ 0.196423   │ -1.06983   │
│ 4     │ 16224.0     │ 1483.3    │ 2.54687e5    │ 0.233977   │ -1.05268   │
│ 5     │ 16577.0     │ 1501.55   │ 2.54677e5    │ 0.216471   │ -1.02838   │
│ 6     │ 16240.0     │ 1483.49   │ 253775.0     │ 0.226734   │ -1.03941   │
│ 7     │ 20398.0     │ 1549.19   │ 2.53398e5    │ -0.0993211 │ -1.06261   │
│ 8     │ 20656.0     │ 1569.25   │ 2.52973e5    │ -0.102567  │ -1.03909   │
│ 9     │ 16228.0     │ 1481.15   │ 2.52693e5    │ 0.208483   │ -1.07057   │
│ 10    │ 20746.0     │ 1567.25   │ 2.50858e5    │ -0.130993  │ -1.04543   │
⋮
│ 36455 │ 24827.0     │ 1617.07   │ 60201.4      │ -0.122107  │ -0.341022  │
│ 36456 │ 19507.0     │ 1537.45   │ 60166.2      │ 0.186737   │ -0.333909  │
│ 36457 │ 21758.0     │ 1564.37   │ 59890.1      │ 0.0457846  │ -0.378508  │
│ 36458 │ 24500.0     │ 1597.67   │ 59526.9      │ -0.20394   │ -0.237984  │
│ 36459 │ 26683.0     │ 1635.39   │ 59295.3      │ -0.421122  │ -0.0764403 │
│ 36460 │ 18073.0     │ 1502.66   │ 59150.5      │ 0.147996   │ -0.255444  │
│ 36461 │ 24048.0     │ 1589.56   │ 57980.5      │ -0.260615  │ -0.214087  │
│ 36462 │ 21177.0     │ 1561.05   │ 57386.6      │ 0.202771   │ -0.274327  │
│ 36463 │ 23708.0     │ 1594.38   │ 57107.4      │ 0.0340928  │ -0.227851  │
│ 36464 │ 20273.0     │ 1540.3    │ 57040.0      │ 0.0324198  │ -0.338027  │
│ 36465 │ 16515.0     │ 1483.84   │ 56886.7      │ 0.228689   │ -0.291753  │

In [86]:
histogram(teamBattles[Int(teamNumber[Int(sumStatsVariance[1, 6]), Int(sumStatsVariance[1, 7]), Int(sumStatsVariance[1, 8])]),:], bins = 200, color = poison, label = "#1 " * sumStatsVariance[1, 9] * ", " * sumStatsVariance[1, 10] * ", " * sumStatsVariance[1, 11])
histogram!(teamBattles[Int(teamNumber[Int(sumStatsVariance[numTeams, 6]), Int(sumStatsVariance[numTeams, 7]), Int(sumStatsVariance[numTeams, 8])]),:], bins = 50, color = normal, label = "#12180 " * sumStatsVariance[numTeams, 9] * ", " * sumStatsVariance[numTeams, 10] * ", " * sumStatsVariance[numTeams, 11])
vline!([1500], color = :red, label = "W/L Cutoff")

In [87]:
avgVar = zeros(numMons, 2)
i = 1
for mon1 = 1:numMons , mon2 = 1:(numMons - 1) , mon3 = (mon2 + 1):numMons
    if mon1 != mon2 && mon1 != mon3 && !isRestricted(mon1, mon2, mon3)
        avgVar[mon1, 1] += summaryStats[i, 3]
        avgVar[mon2, 1] += summaryStats[i, 3]
        avgVar[mon3, 1] += summaryStats[i, 3]
        i += 1
    end
end
for i = 1:numMons
    avgVar[i, 2] = i
end
avgVar[:, 1] ./ (numTeams / (numMons / 3.0))

avgVarSorted = sortslices(avgVar, by=x->x[1], dims = 1, rev = true)

nameAvgVar = Array{String}(undef, numMons, 1)
for i = 1:numMons
    nameAvgVar[i, 1] = pvpokeRanks[Int(avgVarSorted[i, 2])]["speciesName"]
end

avgVarSorted = hcat(avgVarSorted, nameAvgVar)

avgVarSorted = DataFrame(avgVarSorted)

rename!(avgVarSorted, Symbol("x1")=>Symbol("Avg Variance"))
rename!(avgVarSorted, Symbol("x2")=>Symbol("Rank"))
rename!(avgVarSorted, Symbol("x3")=>Symbol("Name"))

45×3 DataFrame
│ Row │ Avg Variance │ Rank │ Name             │
│     │ Any          │ Any  │ Any              │
├─────┼──────────────┼──────┼──────────────────┤
│ 1   │ 4.61125e8    │ 45.0 │ Relicanth        │
│ 2   │ 4.55287e8    │ 36.0 │ Sudowoodo        │
│ 3   │ 4.53449e8    │ 39.0 │ Weepinbell       │
│ 4   │ 4.52479e8    │ 24.0 │ Victreebel       │
│ 5   │ 4.42601e8    │ 25.0 │ Gloom            │
│ 6   │ 4.36126e8    │ 44.0 │ Houndoom         │
│ 7   │ 4.20573e8    │ 18.0 │ Castform (Sunny) │
│ 8   │ 4.17986e8    │ 34.0 │ Wormadam (Plant) │
│ 9   │ 4.0746e8     │ 22.0 │ Whiscash         │
│ 10  │ 4.01631e8    │ 23.0 │ Torkoal          │
⋮
│ 35  │ 2.82952e8    │ 28.0 │ Charmeleon       │
│ 36  │ 2.77537e8    │ 41.0 │ Grotle           │
│ 37  │ 2.73455e8    │ 5.0  │ Swampert         │
│ 38  │ 2.57095e8    │ 16.0 │ Blaziken         │
│ 39  │ 2.50452e8    │ 4.0  │ Charizard        │
│ 40  │ 2.49498e8    │ 10.0 │ Ivysaur          │
│ 41  │ 2.47247e8    │ 12.0 │ Blastoise        │
│ 42  │ 2.37802e8    │ 21.0 │ Typhlosion       │
│ 43  │ 2.31026e8    │ 31.0 │ Sceptile         │
│ 44  │ 2.2963e8     │ 3.0  │ Meganium         │
│ 45  │ 2.27987e8    │ 1.0  │ Venusaur         │

In [88]:
plot(avgVar[:, 1], avgNumOfWins[:, 1], seriestype=:scatter, label = "Average Variance vs. Num of Wins")

## Skewness

Skewness is a little different in that on either end its not more skewed and less skewed, but rather skewed in one direction or the other. This is sort of similar to average score in what it ends up being, but the teams are not as good by that metric, because its specifically looking for skewness.

In [89]:
histogram(summaryStats[:, 4], label = "Skewness")

In [90]:
sumStatsSkewness = sortslices(summaryStats, by=x->x[4], dims = 1, rev = false)

names1 = Array{String}(undef, numTeams, 1)
for i = 1:numTeams
    names1[i, 1] = pvpokeRanks[Int(sumStatsSkewness[i, 6])]["speciesName"]
end

names2 = Array{String}(undef, numTeams, 1)
for i = 1:numTeams
    names2[i, 1] = pvpokeRanks[Int(sumStatsSkewness[i, 7])]["speciesName"]
end

names3 = Array{String}(undef, numTeams, 1)
for i = 1:numTeams
    names3[i, 1] = pvpokeRanks[Int(sumStatsSkewness[i, 8])]["speciesName"]
end

sumStatsSkewness = hcat(sumStatsSkewness, names1)
sumStatsSkewness = hcat(sumStatsSkewness, names2)
sumStatsSkewness = hcat(sumStatsSkewness, names3)

sumStatsSkewness = DataFrame(sumStatsSkewness)

rename!(sumStatsSkewness, Symbol("x1")=>Symbol("Num of Wins")); rename!(sumStatsSkewness, Symbol("x2")=>Symbol("Avg Score")); rename!(sumStatsSkewness, Symbol("x3")=>Symbol("Avg Variance")); rename!(sumStatsSkewness, Symbol("x4")=>Symbol("Avg Skew")); rename!(sumStatsSkewness, Symbol("x5")=>Symbol("Avg Kurt")); rename!(sumStatsSkewness, Symbol("x6")=>Symbol("Rank Mon 1")); rename!(sumStatsSkewness, Symbol("x7")=>Symbol("Rank Mon 2")); rename!(sumStatsSkewness, Symbol("x8")=>Symbol("Rank Mon 3")); rename!(sumStatsSkewness, Symbol("x9")=>Symbol("Mon 1")); rename!(sumStatsSkewness, Symbol("x10")=>Symbol("Mon 2")); rename!(sumStatsSkewness, Symbol("x11")=>Symbol("Mon 3"))

36465×11 DataFrame. Omitted printing of 6 columns
│ Row   │ Num of Wins │ Avg Score │ Avg Variance │ Avg Skew  │ Avg Kurt  │
│       │ Any         │ Any       │ Any          │ Any       │ Any       │
├───────┼─────────────┼───────────┼──────────────┼───────────┼───────────┤
│ 1     │ 25640.0     │ 1623.37   │ 1.03516e5    │ -0.732971 │ 0.454787  │
│ 2     │ 27077.0     │ 1656.49   │ 84569.6      │ -0.706471 │ 0.463672  │
│ 3     │ 25861.0     │ 1655.16   │ 1.16397e5    │ -0.671202 │ 0.265493  │
│ 4     │ 27481.0     │ 1688.82   │ 97018.2      │ -0.661953 │ 0.223251  │
│ 5     │ 26577.0     │ 1653.93   │ 96330.7      │ -0.653523 │ 0.412366  │
│ 6     │ 25224.0     │ 1631.07   │ 1.10036e5    │ -0.651578 │ 0.210006  │
│ 7     │ 27378.0     │ 1693.72   │ 1.0315e5     │ -0.643767 │ 0.254803  │
│ 8     │ 26312.0     │ 1660.89   │ 1.10134e5    │ -0.637239 │ 0.25585   │
│ 9     │ 27263.0     │ 1661.1    │ 83094.6      │ -0.62772  │ 0.43748   │
│ 10    │ 25176.0     │ 1614.25   │ 1.0456e5     │ -0.626127 │ 0.250947  │
⋮
│ 36455 │ 11055.0     │ 1347.82   │ 1.44864e5    │ 0.660424  │ -0.252622 │
│ 36456 │ 11154.0     │ 1349.51   │ 1.44353e5    │ 0.665587  │ -0.295866 │
│ 36457 │ 9913.0      │ 1317.52   │ 1.21443e5    │ 0.665716  │ -0.308157 │
│ 36458 │ 11492.0     │ 1371.09   │ 1.45898e5    │ 0.66941   │ -0.238595 │
│ 36459 │ 11094.0     │ 1363.21   │ 1.31356e5    │ 0.670967  │ -0.313161 │
│ 36460 │ 11252.0     │ 1353.58   │ 1.41235e5    │ 0.675577  │ -0.263997 │
│ 36461 │ 12137.0     │ 1395.84   │ 130426.0     │ 0.682012  │ -0.38153  │
│ 36462 │ 11949.0     │ 1387.29   │ 1.28898e5    │ 0.687277  │ -0.305788 │
│ 36463 │ 10892.0     │ 1342.63   │ 1.4131e5     │ 0.688253  │ -0.213223 │
│ 36464 │ 9509.0      │ 1290.68   │ 1.14537e5    │ 0.691151  │ -0.279432 │
│ 36465 │ 10253.0     │ 1353.1    │ 96883.2      │ 0.717236  │ -0.146573 │

In [91]:
histogram(teamBattles[Int(teamNumber[Int(sumStatsSkewness[1, 6]), Int(sumStatsSkewness[1, 7]), Int(sumStatsSkewness[1, 8])]),:], bins = 100, color = dark, label = "#1 " * sumStatsSkewness[1, 9] * ", " * sumStatsSkewness[1, 10] * ", " * sumStatsSkewness[1, 11])
histogram!(teamBattles[Int(teamNumber[Int(sumStatsSkewness[12180, 6]), Int(sumStatsSkewness[12180, 7]), Int(sumStatsSkewness[12180, 8])]),:], bins = 100, color = normal, label = "#12180 " * sumStatsSkewness[12180, 9] * ", " * sumStatsSkewness[12180, 10] * ", " * sumStatsSkewness[12180, 11])
vline!([1500], color = :red, label = "W/L Cutoff")

In [92]:
avgSkew = zeros(numMons, 2)
i = 1
for mon1 = 1:numMons , mon2 = 1:(numMons - 1) , mon3 = (mon2 + 1):numMons
    if mon1 != mon2 && mon1 != mon3 && !isRestricted(mon1, mon2, mon3)
        avgSkew[mon1, 1] += summaryStats[i, 4]
        avgSkew[mon2, 1] += summaryStats[i, 4]
        avgSkew[mon3, 1] += summaryStats[i, 4]
        i += 1
    end
end
for i = 1:numMons
    avgSkew[i, 2] = i
end
avgSkew[:, 1] ./ (numTeams / (numMons / 3.0))

avgSkewSorted = sortslices(avgSkew, by=x->x[1], dims = 1, rev = false)

nameAvgSkew = Array{String}(undef, numMons, 1)
for i = 1:numMons
    nameAvgSkew[i, 1] = pvpokeRanks[Int(avgSkewSorted[i, 2])]["speciesName"]
end

avgSkewSorted = hcat(avgSkewSorted, nameAvgSkew)

avgSkewSorted = DataFrame(avgSkewSorted)

rename!(avgSkewSorted, Symbol("x1")=>Symbol("Avg Skewness"))
rename!(avgSkewSorted, Symbol("x2")=>Symbol("Rank"))
rename!(avgSkewSorted, Symbol("x3")=>Symbol("Name"))

45×3 DataFrame
│ Row │ Avg Skewness │ Rank │ Name             │
│     │ Any          │ Any  │ Any              │
├─────┼──────────────┼──────┼──────────────────┤
│ 1   │ -616.463     │ 22.0 │ Whiscash         │
│ 2   │ -406.462     │ 30.0 │ Politoed         │
│ 3   │ -364.396     │ 5.0  │ Swampert         │
│ 4   │ -359.182     │ 42.0 │ Cradily          │
│ 5   │ -274.456     │ 2.0  │ Dragonair        │
│ 6   │ -264.275     │ 45.0 │ Relicanth        │
│ 7   │ -263.615     │ 23.0 │ Torkoal          │
│ 8   │ -250.514     │ 32.0 │ Castform (Rainy) │
│ 9   │ -228.067     │ 36.0 │ Sudowoodo        │
│ 10  │ -217.068     │ 15.0 │ Drapion          │
⋮
│ 35  │ 212.146      │ 26.0 │ Piloswine        │
│ 36  │ 212.282      │ 14.0 │ Froslass         │
│ 37  │ 225.497      │ 6.0  │ Kingdra          │
│ 38  │ 264.213      │ 25.0 │ Gloom            │
│ 39  │ 313.065      │ 8.0  │ Venomoth         │
│ 40  │ 343.262      │ 41.0 │ Grotle           │
│ 41  │ 422.383      │ 39.0 │ Weepinbell       │
│ 42  │ 442.097      │ 35.0 │ Dustox           │
│ 43  │ 461.358      │ 33.0 │ Beedrill         │
│ 44  │ 472.729      │ 24.0 │ Victreebel       │
│ 45  │ 509.824      │ 34.0 │ Wormadam (Plant) │

In [93]:
plot(avgNumOfWins[:, 1], avgSkew[:, 1], seriestype=:scatter, label = "Average Skewness vs. Num of Wins")

## Kurtosis

This is one where not only does it not matter a whole lot for team decision making, but it is also not an incredibly well known statistical measure. Basically, kurtosis means the contribution from the tails (the part of the distribution not at the center). The Wikipedia articles on all of these statistical measures are pretty in-depth and can let you know anything you want to about how they work. I'm including these here because I think its interesting, and the teams' distributions at either ends are a rather interesting shape as well.

In [94]:
histogram(summaryStats[:, 5], label = "Kurtosis")

In [95]:
sumStatsKurtosis = sortslices(summaryStats, by=x->x[5], dims = 1, rev = false)

names1 = Array{String}(undef, numTeams, 1)
for i = 1:numTeams
    names1[i, 1] = pvpokeRanks[Int(sumStatsKurtosis[i, 6])]["speciesName"]
end

names2 = Array{String}(undef, numTeams, 1)
for i = 1:numTeams
    names2[i, 1] = pvpokeRanks[Int(sumStatsKurtosis[i, 7])]["speciesName"]
end

names3 = Array{String}(undef, numTeams, 1)
for i = 1:numTeams
    names3[i, 1] = pvpokeRanks[Int(sumStatsKurtosis[i, 8])]["speciesName"]
end

sumStatsKurtosis = hcat(sumStatsKurtosis, names1)
sumStatsKurtosis = hcat(sumStatsKurtosis, names2)
sumStatsKurtosis = hcat(sumStatsKurtosis, names3)

sumStatsKurtosis = DataFrame(sumStatsKurtosis)

rename!(sumStatsKurtosis, Symbol("x1")=>Symbol("Num of Wins")); rename!(sumStatsKurtosis, Symbol("x2")=>Symbol("Avg Score")); rename!(sumStatsKurtosis, Symbol("x3")=>Symbol("Avg Variance")); rename!(sumStatsKurtosis, Symbol("x4")=>Symbol("Avg Skew")); rename!(sumStatsKurtosis, Symbol("x5")=>Symbol("Avg Kurt")); rename!(sumStatsKurtosis, Symbol("x6")=>Symbol("Rank Mon 1")); rename!(sumStatsKurtosis, Symbol("x7")=>Symbol("Rank Mon 2")); rename!(sumStatsKurtosis, Symbol("x8")=>Symbol("Rank Mon 3")); rename!(sumStatsKurtosis, Symbol("x9")=>Symbol("Mon 1")); rename!(sumStatsKurtosis, Symbol("x10")=>Symbol("Mon 2")); rename!(sumStatsKurtosis, Symbol("x11")=>Symbol("Mon 3"))

36465×11 DataFrame. Omitted printing of 6 columns
│ Row   │ Num of Wins │ Avg Score │ Avg Variance │ Avg Skew  │ Avg Kurt │
│       │ Any         │ Any       │ Any          │ Any       │ Any      │
├───────┼─────────────┼───────────┼──────────────┼───────────┼──────────┤
│ 1     │ 15421.0     │ 1417.38   │ 1.9472e5     │ 0.174295  │ -1.23941 │
│ 2     │ 15430.0     │ 1427.76   │ 1.63629e5    │ 0.150921  │ -1.23034 │
│ 3     │ 16080.0     │ 1466.09   │ 1.71542e5    │ 0.134519  │ -1.22121 │
│ 4     │ 16578.0     │ 1509.08   │ 1.37536e5    │ 0.189044  │ -1.2183  │
│ 5     │ 16085.0     │ 1476.74   │ 1.90377e5    │ 0.14787   │ -1.21764 │
│ 6     │ 16047.0     │ 1469.78   │ 1.42797e5    │ 0.211273  │ -1.20327 │
│ 7     │ 15472.0     │ 1438.56   │ 181738.0     │ 0.165605  │ -1.20248 │
│ 8     │ 16719.0     │ 1512.16   │ 1.67334e5    │ 0.15671   │ -1.19585 │
│ 9     │ 16500.0     │ 1494.69   │ 1.30461e5    │ 0.155732  │ -1.19412 │
│ 10    │ 15804.0     │ 1457.18   │ 1.97345e5    │ 0.164695  │ -1.19036 │
⋮
│ 36455 │ 27378.0     │ 1693.72   │ 1.0315e5     │ -0.643767 │ 0.254803 │
│ 36456 │ 26312.0     │ 1660.89   │ 1.10134e5    │ -0.637239 │ 0.25585  │
│ 36457 │ 25861.0     │ 1655.16   │ 1.16397e5    │ -0.671202 │ 0.265493 │
│ 36458 │ 27006.0     │ 1672.73   │ 95296.7      │ -0.624541 │ 0.267551 │
│ 36459 │ 25835.0     │ 1640.18   │ 97889.8      │ -0.480234 │ 0.269966 │
│ 36460 │ 27791.0     │ 1694.64   │ 99462.7      │ -0.504259 │ 0.304305 │
│ 36461 │ 26894.0     │ 1650.49   │ 80746.9      │ -0.505072 │ 0.380041 │
│ 36462 │ 26577.0     │ 1653.93   │ 96330.7      │ -0.653523 │ 0.412366 │
│ 36463 │ 27263.0     │ 1661.1    │ 83094.6      │ -0.62772  │ 0.43748  │
│ 36464 │ 25640.0     │ 1623.37   │ 1.03516e5    │ -0.732971 │ 0.454787 │
│ 36465 │ 27077.0     │ 1656.49   │ 84569.6      │ -0.706471 │ 0.463672 │

In [96]:
histogram(teamBattles[Int(teamNumber[Int(sumStatsKurtosis[1, 6]), Int(sumStatsKurtosis[1, 7]), Int(sumStatsKurtosis[1, 8])]),:], bins = 100, color = poison, label = "#1 " * sumStatsKurtosis[1, 9] * ", " * sumStatsKurtosis[1, 10] * ", " * sumStatsKurtosis[1, 11])
histogram!(teamBattles[Int(teamNumber[Int(sumStatsKurtosis[numTeams, 6]), Int(sumStatsKurtosis[numTeams, 7]), Int(sumStatsKurtosis[numTeams, 8])]),:], bins = 100, color = normal, label = "#12180 " * sumStatsKurtosis[numTeams, 9] * ", " * sumStatsKurtosis[numTeams, 10] * ", " * sumStatsKurtosis[numTeams, 11])
vline!([1500], color = :red, label = "W/L Cutoff")

In [97]:
avgKurt = zeros(numMons, 2)
i = 1
for mon1 = 1:numMons , mon2 = 1:(numMons - 1) , mon3 = (mon2 + 1):numMons
    if mon1 != mon2 && mon1 != mon3 && !isRestricted(mon1, mon2, mon3)
        avgKurt[mon1, 1] += summaryStats[i, 5]
        avgKurt[mon2, 1] += summaryStats[i, 5]
        avgKurt[mon3, 1] += summaryStats[i, 5]
        i += 1
    end
end
for i = 1:numMons
    avgKurt[i, 2] = i
end
avgKurt[:, 1] ./ (numTeams / (numMons / 3.0))

avgKurtSorted = sortslices(avgKurt, by=x->x[1], dims = 1, rev = true)

nameAvgKurt = Array{String}(undef, numMons, 1)
for i = 1:numMons
    nameAvgKurt[i, 1] = pvpokeRanks[Int(avgKurtSorted[i, 2])]["speciesName"]
end

avgKurtSorted = hcat(avgKurtSorted, nameAvgKurt)

avgKurtSorted = DataFrame(avgKurtSorted)

rename!(avgKurtSorted, Symbol("x1")=>Symbol("Avg Kurtosis"))
rename!(avgKurtSorted, Symbol("x2")=>Symbol("Rank"))
rename!(avgKurtSorted, Symbol("x3")=>Symbol("Name"))

45×3 DataFrame
│ Row │ Avg Kurtosis │ Rank │ Name             │
│     │ Any          │ Any  │ Any              │
├─────┼──────────────┼──────┼──────────────────┤
│ 1   │ -935.125     │ 5.0  │ Swampert         │
│ 2   │ -1072.84     │ 21.0 │ Typhlosion       │
│ 3   │ -1084.08     │ 3.0  │ Meganium         │
│ 4   │ -1114.61     │ 1.0  │ Venusaur         │
│ 5   │ -1155.48     │ 31.0 │ Sceptile         │
│ 6   │ -1166.82     │ 16.0 │ Blaziken         │
│ 7   │ -1202.72     │ 41.0 │ Grotle           │
│ 8   │ -1208.2      │ 10.0 │ Ivysaur          │
│ 9   │ -1216.6      │ 4.0  │ Charizard        │
│ 10  │ -1251.71     │ 12.0 │ Blastoise        │
⋮
│ 35  │ -1866.71     │ 27.0 │ Castform (Snowy) │
│ 36  │ -1890.02     │ 13.0 │ Shelgon          │
│ 37  │ -1899.37     │ 18.0 │ Castform (Sunny) │
│ 38  │ -1949.77     │ 23.0 │ Torkoal          │
│ 39  │ -1962.04     │ 17.0 │ Flygon           │
│ 40  │ -2017.74     │ 45.0 │ Relicanth        │
│ 41  │ -2027.91     │ 25.0 │ Gloom            │
│ 42  │ -2029.06     │ 36.0 │ Sudowoodo        │
│ 43  │ -2034.29     │ 43.0 │ Lanturn          │
│ 44  │ -2051.59     │ 39.0 │ Weepinbell       │
│ 45  │ -2059.25     │ 24.0 │ Victreebel       │

In [98]:
plot(avgNumOfWins[:, 1], avgKurt[:, 1], seriestype=:scatter, label = "Average Kurtosis vs. Num of Wins")

# Teams of Six

I'm still in the process of developing this, but for my inital team of six investigation, I'm using an algorithm that chooses the best team of three from that team of six against any team of three.

In [99]:
function maxScore(team)
    maxScores = zeros(numTeams)
    for lead = 1:6, second = 1:5, third = second + 1:6
        if(lead != second && lead != third) && !isRestricted(Int(team[Int(lead)]), Int(team[Int(second)]), Int(team[Int(third)]))
            for i = 1:numTeams
                currentScore = teamBattles[Int(teamNumber[Int(team[Int(lead)]), Int(team[Int(second)]), Int(team[Int(third)])]),i]
                if maxScores[Int(i)] < currentScore
                    maxScores[Int(i)] = currentScore
                end
            end
        end
    end
    return maxScores
end;

Here I compare the top six mons by number of wins and average score (they happen to be the same in this ranking, but in different order), the top six ranked PvPoke mons, the bottom six (of the top 30) PvPoke mons, and the bottom six mons ranked by number of wins

In [100]:
topSix = sort(avgNumOfWinsSorted[1:6, 2])
bottomSix = sort(avgNumOfWinsSorted[(numMons - 5):numMons, 2])

histogram(maxScore([Int(topSix[1]) Int(topSix[2]) Int(topSix[3]) Int(topSix[4]) Int(topSix[5]) Int(topSix[6]) ]), alpha = 0.5, bins = 150, color = :yellow, label = "Top 6 Team Ranked")
histogram!(maxScore([1 2 3 4 5 6]), alpha = 0.5, bins = 150, color = :green, label = "Top 6 PvPoke Ranked")
histogram!(maxScore([25 26 27 28 29 30]), alpha = 0.5, bins = 150, color = :blue, label = "Bottom 6 PvPoke Ranked")
histogram!(maxScore([Int(bottomSix[1]) Int(bottomSix[2]) Int(bottomSix[3]) Int(bottomSix[4]) Int(bottomSix[5]) Int(bottomSix[6]) ]), alpha = 0.5, bins = 150, color = :purple, label = "Bottom 6 Team Ranked")
vline!([1500], color = :red, label = "W/L cutoff")

Here is a histogram of all of the three mon teams (there are sixty) from the top team-ranked six mons, all plotted together. There's a lot going on here, so I'm going to break it down a bit further.

In [101]:
team = [Int(topSix[1]) Int(topSix[2]) Int(topSix[3]) Int(topSix[4]) Int(topSix[5]) Int(topSix[6]) ]
h = histogram(legend = false, alpha = 0.001)
summaryStats2 = zeros(60, 8)
p = x -> (x > 1500.0)
i = 1
for lead = 1:6, second = 1:5, third = second + 1:6
    if(lead != second && lead != third)  && !isRestricted(Int(team[Int(lead)]), Int(team[Int(second)]), Int(team[Int(third)]))
        team1 = teamBattles[Int(teamNumber[Int(team[lead]), Int(team[second]), Int(team[third])]),:]
        numWins = count(p,team1)
        summaryStats2[i, :] = [numWins mean(team1) var(team1) skewness(team1) kurtosis(team1) team[lead] team[second] team[third]]
        i += 1
        histogram!(h, teamBattles[Int(teamNumber[Int(team[lead]), Int(team[second]), Int(team[third])]),:], bins = 50, alpha = 0.5, label = team[lead])
    end
end    
h
vline!([1500], color = :red)

Here are the top teams of three from the six mon team entered above in order of number of wins

In [102]:
sumStatsTeam = sortslices(summaryStats2, by=x->x[1], dims = 1, rev = true)

names1 = Array{String}(undef, 60, 1)
for i = 1:60
    names1[i, 1] = pvpokeRanks[Int(sumStatsTeam[i, 6])]["speciesName"]
end

names2 = Array{String}(undef, 60, 1)
for i = 1:60
    names2[i, 1] = pvpokeRanks[Int(sumStatsTeam[i, 7])]["speciesName"]
end

names3 = Array{String}(undef, 60, 1)
for i = 1:60
    names3[i, 1] = pvpokeRanks[Int(sumStatsTeam[i, 8])]["speciesName"]
end

sumStatsTeam = hcat(sumStatsTeam, names1)
sumStatsTeam = hcat(sumStatsTeam, names2)
sumStatsTeam = hcat(sumStatsTeam, names3)

sumStatsTeam = DataFrame(sumStatsTeam)

rename!(sumStatsTeam, Symbol("x1")=>Symbol("Num of Wins")); rename!(sumStatsTeam, Symbol("x2")=>Symbol("Avg Score")); rename!(sumStatsTeam, Symbol("x3")=>Symbol("Avg Variance")); rename!(sumStatsTeam, Symbol("x4")=>Symbol("Avg Skew")); rename!(sumStatsTeam, Symbol("x5")=>Symbol("Avg Kurt")); rename!(sumStatsTeam, Symbol("x6")=>Symbol("Rank Mon 1")); rename!(sumStatsTeam, Symbol("x7")=>Symbol("Rank Mon 2")); rename!(sumStatsTeam, Symbol("x8")=>Symbol("Rank Mon 3")); rename!(sumStatsTeam, Symbol("x9")=>Symbol("Mon 1")); rename!(sumStatsTeam, Symbol("x10")=>Symbol("Mon 2")); rename!(sumStatsTeam, Symbol("x11")=>Symbol("Mon 3"))

60×11 DataFrame. Omitted printing of 6 columns
│ Row │ Num of Wins │ Avg Score │ Avg Variance │ Avg Skew  │ Avg Kurt   │
│     │ Any         │ Any       │ Any          │ Any       │ Any        │
├─────┼─────────────┼───────────┼──────────────┼───────────┼────────────┤
│ 1   │ 27982.0     │ 1695.06   │ 70375.8      │ -0.27595  │ -0.20201   │
│ 2   │ 27938.0     │ 1725.05   │ 99749.6      │ -0.51737  │ -0.0458774 │
│ 3   │ 27837.0     │ 1691.12   │ 85885.9      │ -0.544382 │ 0.192334   │
│ 4   │ 27677.0     │ 1731.45   │ 1.09189e5    │ -0.426449 │ -0.148006  │
│ 5   │ 27208.0     │ 1700.87   │ 97062.4      │ -0.4341   │ -0.0290169 │
│ 6   │ 27185.0     │ 1702.2    │ 1.04735e5    │ -0.502152 │ -0.143036  │
│ 7   │ 27060.0     │ 1676.92   │ 92706.4      │ -0.550776 │ 0.0339836  │
│ 8   │ 26994.0     │ 1709.02   │ 1.12321e5    │ -0.423142 │ -0.142841  │
│ 9   │ 26931.0     │ 1680.01   │ 86151.9      │ -0.386605 │ -0.0720598 │
│ 10  │ 26866.0     │ 1676.62   │ 76885.6      │ -0.243979 │ -0.383668  │
⋮
│ 50  │ 24580.0     │ 1654.73   │ 1.33391e5    │ -0.358716 │ -0.346818  │
│ 51  │ 24557.0     │ 1638.42   │ 1.27621e5    │ -0.430698 │ -0.322636  │
│ 52  │ 24473.0     │ 1662.01   │ 144022.0     │ -0.372619 │ -0.470912  │
│ 53  │ 24470.0     │ 1649.86   │ 99546.6      │ -0.187569 │ -0.409185  │
│ 54  │ 24363.0     │ 1671.37   │ 1.52565e5    │ -0.280417 │ -0.519888  │
│ 55  │ 24270.0     │ 1640.18   │ 1.17146e5    │ -0.295919 │ -0.218336  │
│ 56  │ 24232.0     │ 1654.94   │ 1.52361e5    │ -0.346509 │ -0.253812  │
│ 57  │ 24196.0     │ 1660.89   │ 1.53164e5    │ -0.329488 │ -0.324215  │
│ 58  │ 24189.0     │ 1647.68   │ 1.36419e5    │ -0.327004 │ -0.401991  │
│ 59  │ 24077.0     │ 1631.36   │ 1.08639e5    │ -0.33903  │ -0.204308  │
│ 60  │ 23973.0     │ 1654.6    │ 1.5448e5     │ -0.350731 │ -0.32373   │

And here's the best and worst from among that lot.

In [103]:
histogram(teamBattles[Int(teamNumber[Int(sumStatsTeam[1, 6]), Int(sumStatsTeam[1, 7]), Int(sumStatsTeam[1, 8])]),:], bins = 100, color = dark, label = "#1 " * sumStatsTeam[1, 9] * ", " * sumStatsTeam[1, 10] * ", " * sumStatsTeam[1, 11])
histogram!(teamBattles[Int(teamNumber[Int(sumStatsTeam[60, 6]), Int(sumStatsTeam[60, 7]), Int(sumStatsTeam[60, 8])]),:], bins = 100, color = normal, label = "#12180 " * sumStatsTeam[60, 9] * ", " * sumStatsTeam[60, 10] * ", " * sumStatsTeam[60, 11])
vline!([1500], color = :red, label = "W/L Cutoff")

And then here's the same thing, but sorted by average score.

In [104]:
sumStatsTeam2 = sortslices(summaryStats2, by=x->x[2], dims = 1, rev = true)

names1 = Array{String}(undef, 60, 1)
for i = 1:60
    names1[i, 1] = pvpokeRanks[Int(sumStatsTeam2[i, 6])]["speciesName"]
end

names2 = Array{String}(undef, 60, 1)
for i = 1:60
    names2[i, 1] = pvpokeRanks[Int(sumStatsTeam2[i, 7])]["speciesName"]
end

names3 = Array{String}(undef, 60, 1)
for i = 1:60
    names3[i, 1] = pvpokeRanks[Int(sumStatsTeam2[i, 8])]["speciesName"]
end

sumStatsTeam2 = hcat(sumStatsTeam2, names1)
sumStatsTeam2 = hcat(sumStatsTeam2, names2)
sumStatsTeam2 = hcat(sumStatsTeam2, names3)

sumStatsTeam2 = DataFrame(sumStatsTeam2)

rename!(sumStatsTeam2, Symbol("x1")=>Symbol("Num of Wins")); rename!(sumStatsTeam2, Symbol("x2")=>Symbol("Avg Score")); rename!(sumStatsTeam2, Symbol("x3")=>Symbol("Avg Variance")); rename!(sumStatsTeam2, Symbol("x4")=>Symbol("Avg Skew")); rename!(sumStatsTeam2, Symbol("x5")=>Symbol("Avg Kurt")); rename!(sumStatsTeam2, Symbol("x6")=>Symbol("Rank Mon 1")); rename!(sumStatsTeam2, Symbol("x7")=>Symbol("Rank Mon 2")); rename!(sumStatsTeam2, Symbol("x8")=>Symbol("Rank Mon 3")); rename!(sumStatsTeam2, Symbol("x9")=>Symbol("Mon 1")); rename!(sumStatsTeam2, Symbol("x10")=>Symbol("Mon 2")); rename!(sumStatsTeam2, Symbol("x11")=>Symbol("Mon 3"))

60×11 DataFrame. Omitted printing of 6 columns
│ Row │ Num of Wins │ Avg Score │ Avg Variance │ Avg Skew  │ Avg Kurt   │
│     │ Any         │ Any       │ Any          │ Any       │ Any        │
├─────┼─────────────┼───────────┼──────────────┼───────────┼────────────┤
│ 1   │ 27677.0     │ 1731.45   │ 1.09189e5    │ -0.426449 │ -0.148006  │
│ 2   │ 27938.0     │ 1725.05   │ 99749.6      │ -0.51737  │ -0.0458774 │
│ 3   │ 26994.0     │ 1709.02   │ 1.12321e5    │ -0.423142 │ -0.142841  │
│ 4   │ 27185.0     │ 1702.2    │ 1.04735e5    │ -0.502152 │ -0.143036  │
│ 5   │ 26304.0     │ 1701.7    │ 1.23956e5    │ -0.423864 │ -0.152061  │
│ 6   │ 27208.0     │ 1700.87   │ 97062.4      │ -0.4341   │ -0.0290169 │
│ 7   │ 25633.0     │ 1700.59   │ 1.30873e5    │ -0.396294 │ -0.507099  │
│ 8   │ 26160.0     │ 1699.29   │ 1.45241e5    │ -0.590727 │ -0.149597  │
│ 9   │ 25852.0     │ 1697.53   │ 149142.0     │ -0.560745 │ -0.249432  │
│ 10  │ 26344.0     │ 1695.58   │ 1.40054e5    │ -0.552018 │ -0.152445  │
⋮
│ 50  │ 24232.0     │ 1654.94   │ 1.52361e5    │ -0.346509 │ -0.253812  │
│ 51  │ 24580.0     │ 1654.73   │ 1.33391e5    │ -0.358716 │ -0.346818  │
│ 52  │ 23973.0     │ 1654.6    │ 1.5448e5     │ -0.350731 │ -0.32373   │
│ 53  │ 24874.0     │ 1650.67   │ 1.07213e5    │ -0.296789 │ -0.469379  │
│ 54  │ 24470.0     │ 1649.86   │ 99546.6      │ -0.187569 │ -0.409185  │
│ 55  │ 25068.0     │ 1648.17   │ 98838.3      │ -0.241328 │ -0.318992  │
│ 56  │ 24189.0     │ 1647.68   │ 1.36419e5    │ -0.327004 │ -0.401991  │
│ 57  │ 24864.0     │ 1645.34   │ 1.23392e5    │ -0.47268  │ -0.206452  │
│ 58  │ 24270.0     │ 1640.18   │ 1.17146e5    │ -0.295919 │ -0.218336  │
│ 59  │ 24557.0     │ 1638.42   │ 1.27621e5    │ -0.430698 │ -0.322636  │
│ 60  │ 24077.0     │ 1631.36   │ 1.08639e5    │ -0.33903  │ -0.204308  │

In [105]:
histogram(teamBattles[Int(teamNumber[Int(sumStatsTeam2[1, 6]), Int(sumStatsTeam2[1, 7]), Int(sumStatsTeam2[1, 8])]),:], bins = 100, color = water, label = "#1 " * sumStatsTeam2[1, 9] * ", " * sumStatsTeam2[1, 10] * ", " * sumStatsTeam2[1, 11])
histogram!(teamBattles[Int(teamNumber[Int(sumStatsTeam2[60, 6]), Int(sumStatsTeam2[60, 7]), Int(sumStatsTeam2[60, 8])]),:], bins = 100, color = normal, label = "#12180 " * sumStatsTeam2[60, 9] * ", " * sumStatsTeam2[60, 10] * ", " * sumStatsTeam2[60, 11])
vline!([1500], color = :red, label = "W/L Cutoff")

# Counters

This algorithm ranks mons as the best counters against any particular three mon team. For now, I've got the top team by number of wins inputted (Suicune, Alolan Ninetales, Alolan Marowak).

In [106]:
indices = zeros(numTeams, 3)
i = 1
for mon1 = 1:numMons , mon2 = 1:(numMons - 1) , mon3 = (mon2 + 1):numMons
    if mon1 != mon2 && mon1 != mon3 && !isRestricted(mon1, mon2, mon3)
        indices[i, 1] = mon1
        indices[i, 2] = mon2
        indices[i, 3] = mon3
        i += 1
    end
end

homeTeam = hcat(teamBattles[Int(teamNumber[6, 4, 16]),:], indices)

counters = zeros(numMons, 2)
for i = 1:numTeams
    for j = 1:numMons
        if(homeTeam[i, 2] == j || homeTeam[i, 3] == j || homeTeam[i, 4] == j)
            counters[j, 1] += 1500 - homeTeam[i, 1]
            counters[j, 2] = j
        end
    end
end

countersSorted = sortslices(counters, by=x->x[1], dims = 1, rev = true)

nameCounters = Array{String}(undef, numMons, 1)
for i = 1:numMons
    nameCounters[i, 1] = pvpokeRanks[Int(countersSorted[i, 2])]["speciesName"]
end

countersSorted = hcat(countersSorted, nameCounters)

BoundsError: BoundsError: attempt to access 36465×36465 Array{Float64,2} at index [0, Base.Slice(Base.OneTo(36465))]

## Roles

### Lead

This algorithm is intended to find the best leads on average, and the table below is sorted by average score

In [107]:
leadMeanScore = zeros(numMons, 2)
leadNumWins = zeros(numMons, 2)
i = 0
p = x -> (x > 1500.0)
for mon1 = 1:numMons , mon2 = 1:(numMons - 1) , mon3 = (mon2 + 1):numMons
    if mon1 != mon2 && mon1 != mon3 && !isRestricted(mon1, mon2, mon3)
        team = teamBattles[Int(teamNumber[mon1, mon2, mon3]), :]
        leadMeanScore[mon1, 1] += mean(team)
        leadNumWins[mon1, 1] += count(p, team)
        i += 1
    end
end

for j = 1:numMons
    leadMeanScore[j, 2] = j
    leadNumWins[j, 2] = j
end
leadMeanScore[:, 1] = leadMeanScore[:, 1]./(i / Float64(numMons))

leadScoreSorted = sortslices(leadMeanScore, by=x->x[1], dims = 1, rev = true)

nameLeads = Array{String}(undef, numMons, 1)
for i = 1:numMons
    nameLeads[i, 1] = pvpokeRanks[Int(leadScoreSorted[i, 2])]["speciesName"]
end

leadScoreSorted = hcat(leadScoreSorted, nameLeads)

45×3 Array{Any,2}:
 1782.94    2.0  "Dragonair"       
 1740.09   20.0  "Banette"         
 1733.63    7.0  "Lapras"          
 1728.66   22.0  "Whiscash"        
 1726.55   30.0  "Politoed"        
 1707.45   45.0  "Relicanth"       
 1698.7    32.0  "Castform (Rainy)"
 1692.4     9.0  "Haunter"         
 1691.07   17.0  "Flygon"          
 1686.51   36.0  "Sudowoodo"       
 1675.34   15.0  "Drapion"         
 1668.31   38.0  "Sealeo"          
 1659.98   44.0  "Houndoom"        
    ⋮                              
 1509.5    34.0  "Wormadam (Plant)"
 1104.06    5.0  "Swampert"        
 1075.86    4.0  "Charizard"       
 1058.63   16.0  "Blaziken"        
 1055.69    3.0  "Meganium"        
 1049.44    1.0  "Venusaur"        
 1034.78   12.0  "Blastoise"       
 1034.11   21.0  "Typhlosion"      
 1020.96   41.0  "Grotle"          
 1011.9    31.0  "Sceptile"        
 1010.37   28.0  "Charmeleon"      
  972.522  10.0  "Ivysaur"         

Same thing, but sorted by number of wins

In [108]:
leadNumWinsSorted = sortslices(leadNumWins, by=x->x[1], dims = 1, rev = true)

nameLeads2 = Array{String}(undef, numMons, 1)
for i = 1:numMons
    nameLeads2[i, 1] = pvpokeRanks[Int(leadNumWinsSorted[i, 2])]["speciesName"]
end

leadNumWinsSorted = hcat(leadNumWinsSorted, nameLeads2)

45×3 Array{Any,2}:
 2.15155e7   2.0  "Dragonair"       
 1.95574e7  20.0  "Banette"         
 1.95184e7  30.0  "Politoed"        
 1.95117e7   7.0  "Lapras"          
 1.95009e7  22.0  "Whiscash"        
 1.83959e7  32.0  "Castform (Rainy)"
 1.83235e7  45.0  "Relicanth"       
 1.79113e7  36.0  "Sudowoodo"       
 1.76904e7  15.0  "Drapion"         
 1.76765e7   9.0  "Haunter"         
 1.70841e7  38.0  "Sealeo"          
 1.69907e7  29.0  "Glalie"          
 1.66756e7  44.0  "Houndoom"        
 ⋮                                  
 1.18137e7  34.0  "Wormadam (Plant)"
 1.11657e7  35.0  "Dustox"          
 1.1139e7    4.0  "Charizard"       
 1.09727e7  16.0  "Blaziken"        
 1.07247e7   1.0  "Venusaur"        
 1.0642e7    3.0  "Meganium"        
 1.0491e7   12.0  "Blastoise"       
 1.04293e7  21.0  "Typhlosion"      
 9.05229e6  28.0  "Charmeleon"      
 8.96641e6  31.0  "Sceptile"        
 8.79734e6  41.0  "Grotle"          
 8.25529e6  10.0  "Ivysaur"         

### Secondary

Here I'm looking at the other role in this model, the non-lead (or secondary) mon. As before, this first table is sorted by average score

In [109]:
secondaryMeanScore = zeros(numMons, 2)
secondaryNumWins = zeros(numMons, 2)
i = 0
p = x -> (x > 1500.0)
for mon1 = 1:numMons , mon2 = 1:(numMons - 1) , mon3 = (mon2 + 1):numMons
    if mon1 != mon2 && mon1 != mon3 && !isRestricted(mon1, mon2, mon3)
        team = teamBattles[Int(teamNumber[mon1, mon2, mon3]), :]
        secondaryMeanScore[mon2, 1] += mean(team)
        secondaryMeanScore[mon3, 1] += mean(team)
        secondaryNumWins[mon2, 1] += count(p, team)
        secondaryNumWins[mon3, 1] += count(p, team)
        i += 1
    end
end
for j = 1:numMons
    secondaryMeanScore[j, 2] = j
    secondaryNumWins[j, 2] = j
end

secondaryScoreSorted = sortslices(secondaryMeanScore, by=x->x[1], dims = 1, rev = true)

nameSecondary = Array{String}(undef, 30, 1)
for i = 1:numMons
    nameSecondary[i, 1] = pvpokeRanks[Int(secondaryScoreSorted[i, 2])]["speciesName"]
end

secondaryScoreSorted = hcat(secondaryScoreSorted, nameSecondary)

BoundsError: BoundsError: attempt to access 30×1 Array{String,2} at index [31, 1]

And this list is the best secondary mons by number of wins

In [110]:
secondaryNumWinSorted = sortslices(secondaryNumWins, by=x->x[1], dims = 1, rev = true)

nameSecondary2 = Array{String}(undef, numMons, 1)
for i = 1:numMons
    nameSecondary2[i, 1] = pvpokeRanks[Int(secondaryNumWinSorted[i, 2])]["speciesName"]
end

secondaryNumWinSorted = hcat(secondaryNumWinSorted, nameSecondary2)

45×3 Array{Any,2}:
 3.56837e7   2.0  "Dragonair"       
 3.53411e7  22.0  "Whiscash"        
 3.50656e7  20.0  "Banette"         
 3.47844e7  17.0  "Flygon"          
 3.46089e7   7.0  "Lapras"          
 3.43635e7  45.0  "Relicanth"       
 3.42488e7  30.0  "Politoed"        
 3.36485e7  32.0  "Castform (Rainy)"
 3.35616e7   9.0  "Haunter"         
 3.33356e7  36.0  "Sudowoodo"       
 3.29573e7  44.0  "Houndoom"        
 3.28629e7  39.0  "Weepinbell"      
 3.28384e7  25.0  "Gloom"           
 ⋮                                  
 2.71429e7  34.0  "Wormadam (Plant)"
 2.30535e7   5.0  "Swampert"        
 2.18168e7   4.0  "Charizard"       
 2.10915e7  16.0  "Blaziken"        
 2.10465e7   3.0  "Meganium"        
 2.07207e7   1.0  "Venusaur"        
 2.01876e7  12.0  "Blastoise"       
 2.01437e7  41.0  "Grotle"          
 2.00003e7  21.0  "Typhlosion"      
 1.98201e7  31.0  "Sceptile"        
 1.94378e7  28.0  "Charmeleon"      
 1.80514e7  10.0  "Ivysaur"         

And finally, here I plot the secondary vs. lead number of wins, with each mon being a dot.

In [111]:
plot(leadNumWins[:, 1], secondaryNumWins[:, 1], seriestype=:scatter, title = "Secondary Num Wins vs. Lead Num Wins", legend = false)

## Clustering

In [131]:
kIndividual = 10
individualRanks = zeros(numMons, numMons)
for i = 1:numMons, j = 1:numMons
    individualRanks[i, j] = rankings[i, (j + 1)]
end
individualKMeans = kmeans(individualRanks, kIndividual; maxiter=200, display=:iter)
individualClusters = Array{String}(undef, kIndividual, maximum(counts(individualKMeans)))
individualAssignments = assignments(individualKMeans)
for i = 1:numMons
    for j = 1:maximum(counts(individualKMeans))
        try individualClusters[individualAssignments[i], j]
            
        catch 
            individualClusters[individualAssignments[i], j] = rankings[i, 1]
            break
        end
    end 
end
for i = 1:kIndividual, j = 1:maximum(counts(individualKMeans))
    try individualClusters[i, j]
            
    catch 
        individualClusters[i, j] = ""
    end
end
DataFrame(individualClusters)

  Iters               objv        objv-change | affected 
-------------------------------------------------------------
      0       4.240709e+07
      1       2.452484e+07      -1.788225e+07 |        0
      2       2.452484e+07       0.000000e+00 |        0
K-means converged with 2 iterations (objv = 2.4524837771428585e7)


10×7 DataFrame. Omitted printing of 4 columns
│ Row │ x1                  │ x2                        │ x3                  │
│     │ String              │ String                    │ String              │
├─────┼─────────────────────┼───────────────────────────┼─────────────────────┤
│ 1   │ Venomoth C+SW/PF    │ Froslass PS+A/SB          │ Drapion IF+C/AT     │
│ 2   │ Victreebel RL+LB/SB │ Gloom RL+R/SB             │ Weepinbell RL+SB/SB │
│ 3   │ Haunter SC+SP/SB    │ Banette SC+SB/R           │                     │
│ 4   │ Meganium VW+FP/E    │ Sceptile FC+LB/E          │ Grotle RL+BS/R      │
│ 5   │ Venusaur VW+FP/SB   │ Ivysaur VW+PW/SB          │ Beedrill PJ+XS/SB   │
│ 6   │ Blastoise WG+HC/IB  │ Castform (Rainy) WG+WBW/T │ Lanturn WG+T/HP     │
│ 7   │ Swampert MS+HC/E    │ Whiscash MS+MB/B          │ Politoed MS+S/E     │
│ 8   │ Charizard FS+BB/DC  │ Castform (Sunny) E+WBF/SB │ Torkoal FS+E/SB     │
│ 9   │ Dragonair DB+AT/R   │ Kingdra DB+O/HP           │ Skuntank PJ+C/F     │
│ 10  │ Lapras IS+S/SB      │ Blaziken C+BK/BB          │ Typhlosion SC+BB/SB │